## DataFrames and queries

Simple example ... a stochastic simulation for the Euler number:

In [1]:
function simulate_e()
    jumps = Float64[]
    while true
        push!(jumps, rand())  # rand is uniform in [0, 1)
        sum(jumps) > 1.0 && return jumps
    end
end

simulate_e (generic function with 1 method)

In [2]:
using DataFrames

df = DataFrame()
for i in 1:10^7
    push!(df, (id=i, pos=simulate_e()))
end

df

10000000×2 DataFrame
      Row │ id        pos                               
          │ Int64     Array…                            
──────────┼─────────────────────────────────────────────
        1 │        1  [0.516096, 0.934176]
        2 │        2  [0.46018, 0.763303]
        3 │        3  [0.64684, 0.801719]
        4 │        4  [0.529929, 0.0473512, 0.592272]
        5 │        5  [0.783905, 0.0286463, 0.276638]
        6 │        6  [0.186182, 0.282674, 0.864622]
        7 │        7  [0.629974, 0.044148, 0.526674]
        8 │        8  [0.171189, 0.142866, 0.285596, 0…
        9 │        9  [0.289239, 0.129265, 0.261839, 0…
       10 │       10  [0.901123, 0.925148]
       11 │       11  [0.251207, 0.0977757, 0.918136]
    ⋮     │    ⋮                      ⋮
  9999991 │  9999991  [0.135313, 0.321574, 0.339463, 0…
  9999992 │  9999992  [0.819241, 0.43355]
  9999993 │  9999993  [0.348306, 0.411376, 0.492071]
  9999994 │  9999994  [0.846463, 0.833353]
  9999995 │  9999995  [0.464502, 0.318312, 0.76365]
  9999996 │  9999996  [0.733254, 0.932288]
  9999997 │  9999997  [0.396699, 0.583513, 0.606831]
  9999998 │  9999998  [0.5218, 0.0657931, 0.580902]
  9999999 │  9999999  [0.979884, 0.285146]
 10000000 │ 10000000  [0.539518, 0.631119]
                                    9999979 rows omitted

In [3]:
transform!(df, :pos => ByRow(length) => :jumps)

10000000×3 DataFrame
      Row │ id        pos                                jumps 
          │ Int64     Array…                             Int64 
──────────┼────────────────────────────────────────────────────
        1 │        1  [0.516096, 0.934176]                   2
        2 │        2  [0.46018, 0.763303]                    2
        3 │        3  [0.64684, 0.801719]                    2
        4 │        4  [0.529929, 0.0473512, 0.592272]        3
        5 │        5  [0.783905, 0.0286463, 0.276638]        3
        6 │        6  [0.186182, 0.282674, 0.864622]         3
        7 │        7  [0.629974, 0.044148, 0.526674]         3
        8 │        8  [0.171189, 0.142866, 0.285596, 0…      5
        9 │        9  [0.289239, 0.129265, 0.261839, 0…      4
       10 │       10  [0.901123, 0.925148]                   2
       11 │       11  [0.251207, 0.0977757, 0.918136]        3
    ⋮     │    ⋮                      ⋮                    ⋮
  9999991 │  9999991  [0.135313, 0.321574, 0.339463, 0…      4
  9999992 │  9999992  [0.819241, 0.43355]                    2
  9999993 │  9999993  [0.348306, 0.411376, 0.492071]         3
  9999994 │  9999994  [0.846463, 0.833353]                   2
  9999995 │  9999995  [0.464502, 0.318312, 0.76365]          3
  9999996 │  9999996  [0.733254, 0.932288]                   2
  9999997 │  9999997  [0.396699, 0.583513, 0.606831]         3
  9999998 │  9999998  [0.5218, 0.0657931, 0.580902]          3
  9999999 │  9999999  [0.979884, 0.285146]                   2
 10000000 │ 10000000  [0.539518, 0.631119]                   2
                                           9999979 rows omitted

In [4]:
mean(df.jumps)

2.7184204

In [5]:
MathConstants.e

ℯ = 2.7182818284590...

In [6]:
using Pipe

# Number of jumps:
jumps_agg = @pipe df |>
                  groupby(_, :jumps, sort=true) |>
                  combine(_, :jumps => length)

10×2 DataFrame
 Row │ jumps  jumps_length 
     │ Int64  Int64        
─────┼─────────────────────
   1 │     2       4999570
   2 │     3       3332899
   3 │     4       1250707
   4 │     5        333519
   5 │     6         69450
   6 │     7         11878
   7 │     8          1727
   8 │     9           219
   9 │    10            30
  10 │    11             1

In [7]:
transform!(jumps_agg,
           :jumps_length => (x -> x ./ sum(x)) => :simulation,
           :jumps => ByRow(x -> (x-1) / factorial(x)) => :theory)

10×4 DataFrame
 Row │ jumps  jumps_length  simulation  theory      
     │ Int64  Int64         Float64     Float64     
─────┼──────────────────────────────────────────────
   1 │     2       4999570   0.499957   0.5
   2 │     3       3332899   0.33329    0.333333
   3 │     4       1250707   0.125071   0.125
   4 │     5        333519   0.0333519  0.0333333
   5 │     6         69450   0.006945   0.00694444
   6 │     7         11878   0.0011878  0.00119048
   7 │     8          1727   0.0001727  0.000173611
   8 │     9           219   2.19e-5    2.20459e-5
   9 │    10            30   3.0e-6     2.48016e-6
  10 │    11             1   1.0e-7     2.50521e-7

## Gaussian process regression

In [8]:
using Stheno

# Generate some synthetic data
N = 100
x = 2π * rand(N)
y = sin.(x) + 0.05*randn(N)

# Construct a squared exponential kernel σ² exp(-||x-x'||^2 / 2l²)
K(l, σ²) = σ² * stretch(EQ(), 1 / l)

# Setup zero-mean GP with this kernel (l = 1.0, σ² = 1.0)
f = GP(K(1.0, 1.0), GPC())

# Sample from this GP (with some IID observation noise)
# which is put on the diagonal of the Kernel
σ²ₙ = 0.05
fx = f(x, σ²ₙ)

# Compute posterior over f
f_posterior = f | Obs(fx, y)

# Plot it all
using Plots
plt = plot();
scatter!(plt, x, y; color=:red, label="");

x_plot = range(-0.5, 6.7; length=1000);
plot!(plt, f_posterior(x_plot); samples=10, label="", color=:blue)

In [9]:
# Hyperparameter optimisation
using Optim
using Zygote

# Unpack hyperparameters (given in log scale)
# Fudge term to avoid nasty zeros ...
unpack(θ) = exp.(θ) .+ 1e-6

# nlml = negative log marginal likelihood (of θ)
function nlml(θ)
    l, σ², σ²ₙ = unpack(θ)
    f = GP(K(l, σ²), GPC()) 
    -logpdf(f(x, σ²ₙ), y)
end

# Optimise using BFGS with adjoint-mode autodiff gradient on nlml
θ0 = randn(3);
results = Optim.optimize(nlml, nlml', θ0, BFGS(); inplace=false)
l_opt, σ²_opt, σ²ₙ_opt = unpack(results.minimizer)

@show σ²_opt
@show l_opt
@show σ²ₙ_opt

# Optimal GP and posterior
f_opt = GP(K(l_opt, σ²_opt), GPC())
f_posterior_opt = f_opt | Obs(f_opt(x, σ²ₙ_opt), y)

# Add to plot ...
plot!(plt, f_posterior_opt(x_plot); samples=10, label="", color=:green)

σ²_opt = 0.5562315745305743
l_opt = 1.5064785044779314
σ²ₙ_opt = 0.0024564687837136147
